# CMIP5 Data Processing

The purpose of this notebook is to process the CMIP5, downscaled collection of climate change simulations for historical moments. The data set extends from 1/1/1951 until 12/31/2099.

- 1/1/1951 through 12/31/2099

The 30-yr, data focus period is:

- 1/1/1981 through 12/31/2010

CMIP5 model results have been downscaled to the NLDAS-2 grid.

## Imports and Parameters

In [1]:
# this tells Jupyter to embed matplotlib plots in the notebook
%matplotlib notebook

In [2]:
import numpy as np
import pandas as pd
import datetime as dt
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib
import shapely as sp
from matplotlib.collections import PatchCollection
from matplotlib.lines import Line2D
from shapely.geometry import Point
from shapely.geometry import Polygon
from IPython.display import display, HTML
import os
from copy import deepcopy
import pyodbc
import sqlalchemy

Custom python code module

In [3]:
import DBA_DClimComp as DBAD

Output directory

In [4]:
OUT_DIR = r'\\augustine.space.swri.edu\jdrive\Groundwater\R8937_Stochastic_CC_Recharge\Da' \
          r'ta\JNotes\Processed\CMIP5'

All of the PRISM data have been placed in a database

For precipitation we have a wet threshold. The precipitation depth must equal or exceed this threshold before being counted as a wet day

In [5]:
WD_THRESH = 0.2   # in mm

## Processing and Aggregation to Monthly and Annual

Our first processing step for precipitation is to aggregate to monthly and calendar year annual values. These should be output to RData structures for seasonal and harmonic analysis in R, spreadsheets for manual examination, and Python pickle files for later loading into Jupyter notebooks.

Make the connection to the DB using a SQL Alchemy engine object

In [6]:
engine = sqlalchemy.create_engine( DBAD.DSN_STRING )

Acquire a Pandas DataFrame for our CMIP5 grid definition

In [7]:
GridSQL = DBAD.createSQLCMIP5Grid()
GridDF = pd.read_sql( GridSQL, engine, index_col=DBAD.FIELDN_ID )

In [8]:
display( HTML( GridDF.to_html() ) )

In [9]:
GridCols = list( GridDF.columns )
GridCols

['Row', 'Col', 'utm_x', 'utm_y', 'DS_Method', 'DS_Resolution']

Acquire a Pandas DataFrame for CMIP5 model definition

In [10]:
ModelSQL = DBAD.createSQLCMIP5Model()
ModelDF = pd.read_sql( ModelSQL, engine, index_col=DBAD.FIELDN_ID )

In [11]:
display( HTML( ModelDF.to_html() ) )

In [12]:
ModelCols = list( ModelDF.columns )
ModelCols

['Result_Ind', 'ICRunNum', 'Scenario_ID', 'CMIP5_Model']

Get our start and end dates and then go through our grid cells, read in the precipitation values for the specified time interval, generate monthly and yearly sums. 

Save all of our DataFrames in dictionaries by Grid Code.

In [27]:
START_DT = dt.datetime( 1981, 1, 1, 0, 0, 0 )
END_DT = dt.datetime( 2010, 12, 31, 0, 0, 0 )

In [28]:
DryDict = dict()
WetDict = dict()

In [35]:
NumGPts = len( GridDF )
NumMods = len( ModelDF )
NumMods, NumGPts

(196, 210)

In [30]:
for jJ in range(1, (NumMods + 1)):
    ModInd = jJ
    for iI in range(1, (NumGPts + 1)):
        GridInd = iI
        GridUTMX = float( GridDF.at[iI, GridCols[2]] )
        GridUTMY = float( GridDF.at[iI, GridCols[3]] )
        # make our joint index
        JntInd = "M%d_%d" % (ModInd, GridInd)
        # now are ready to get our precipitation values
        PreSQL = DBAD.createSQLCMIP5Pre( START_DT, END_DT, iI, jJ )
        PreDF = pd.read_sql( PreSQL, engine, index_col=DBAD.FIELDN_STRDT, 
                             parse_dates=[DBAD.FIELDN_STRDT] )
        if len( PreDF ) < 1:
            #print("No values for %s" % JntInd)
            continue
        PreDF.index.name = DBAD.FIELDN_DT
        PreDF.index = PreDF.index.tz_convert( None )
        # now do the resample 
        MonDF = PreDF.resample( 'MS', axis=0, closed='left', label='left' ).sum()
        AnnDF = PreDF.resample( 'AS', axis=0, closed='left', label='left' ).sum()
        # change the column names
        MonDF.columns = ["Precip_mm"]
        AnnDF.columns = ["Precip_mm"]
        # now make our appends
        GMonDF = MonDF.copy()
        GMonDF.columns = [JntInd]
        GAnnDF = AnnDF.copy()
        GAnnDF.columns = [JntInd]
        # now check where we are
        if (iI == 1) and (jJ == 1):
            AllMonDF = GMonDF.copy()
            AllAnnDF = GAnnDF.copy()
        else:
            AllMonDF = AllMonDF.merge( GMonDF, how='inner', left_index=True, right_index=True)
            AllAnnDF = AllAnnDF.merge( GAnnDF, how='inner', left_index=True, right_index=True)
        # the resampling is done so now want go through and get our counts of contiguous
        #  wet days and contiguous dry days. Also track the start date for the contiguous 
        #  series and track the total depth for wet series and the daily depth within the
        #  wet series.
        cNumDays = len( PreDF )
        inWet = False
        inDry = False
        cWetCnt = 0
        cDryCnt = 0
        DryList = list()
        WetList = list()
        for dD in range( cNumDays ):
            cTSInd = PreDF.index[dD]
            cDT = dt.datetime( cTSInd.year, cTSInd.month, cTSInd.day )
            if dD == 0:
                cWStartDT = cDT
                cDStartDT = cDT
            cPDepth = float( PreDF.at[cTSInd,'Precip_mmpd'] )
            if cPDepth >= WD_THRESH:
                # this is the wet day case
                if inWet:
                    cWetCnt += 1
                    totPrecip += cPDepth
                    dayPreL.append( cPDepth )
                else:
                    inWet = True
                    inDry = False
                    cWStartDT = cDT
                    cWetCnt = 1
                    dayPreL = [ cPDepth ]
                    totPrecip = cPDepth
                    if dD > 0:
                        DryList.append( [ cDStartDT, cDryCnt ] )
                        cDryCnt = 0
            else:
                # this is the dry day case
                if inDry:
                    cDryCnt += 1
                else:
                    inWet = False
                    inDry = True
                    cDStartDT = cDT
                    cDryCnt = 1
                    if dD > 0:
                        WetList.append( [ cWStartDT, cWetCnt, totPrecip, dayPreL ] )
                        cWetCnt = 0
                        totPrecip = 0.0
                        dayPreL = list()
            # end of outer depth if
        # end of the day for
        # check for the last entry
        if inWet:
            WetList.append( [ cWStartDT, cWetCnt, totPrecip, dayPreL ] )
        else:
            DryList.append( [ cDStartDT, cDryCnt ] )
        # add our state analysis lists to our dictionaries
        DryDict[JntInd] = DryList
        WetDict[JntInd] = WetList
    # end of inner for loop
# end of outer for loop

No values for M1_169
No values for M1_170
No values for M1_171
No values for M1_172
No values for M1_173
No values for M1_174
No values for M1_175
No values for M1_176
No values for M1_177
No values for M1_178
No values for M1_179
No values for M1_180
No values for M1_181
No values for M1_182
No values for M1_183
No values for M1_184
No values for M1_185
No values for M1_186
No values for M1_187
No values for M1_188
No values for M1_189
No values for M1_190
No values for M1_191
No values for M1_192
No values for M1_193
No values for M1_194
No values for M1_195
No values for M1_196
No values for M1_197
No values for M1_198
No values for M1_199
No values for M1_200
No values for M1_201
No values for M1_202
No values for M1_203
No values for M1_204
No values for M1_205
No values for M1_206
No values for M1_207
No values for M1_208
No values for M1_209
No values for M1_210
No values for M2_169
No values for M2_170
No values for M2_171
No values for M2_172
No values for M2_173
No values for

No values for M10_181
No values for M10_182
No values for M10_183
No values for M10_184
No values for M10_185
No values for M10_186
No values for M10_187
No values for M10_188
No values for M10_189
No values for M10_190
No values for M10_191
No values for M10_192
No values for M10_193
No values for M10_194
No values for M10_195
No values for M10_196
No values for M10_197
No values for M10_198
No values for M10_199
No values for M10_200
No values for M10_201
No values for M10_202
No values for M10_203
No values for M10_204
No values for M10_205
No values for M10_206
No values for M10_207
No values for M10_208
No values for M10_209
No values for M10_210
No values for M11_169
No values for M11_170
No values for M11_171
No values for M11_172
No values for M11_173
No values for M11_174
No values for M11_175
No values for M11_176
No values for M11_177
No values for M11_178
No values for M11_179
No values for M11_180
No values for M11_181
No values for M11_182
No values for M11_183
No values 

No values for M19_176
No values for M19_177
No values for M19_178
No values for M19_179
No values for M19_180
No values for M19_181
No values for M19_182
No values for M19_183
No values for M19_184
No values for M19_185
No values for M19_186
No values for M19_187
No values for M19_188
No values for M19_189
No values for M19_190
No values for M19_191
No values for M19_192
No values for M19_193
No values for M19_194
No values for M19_195
No values for M19_196
No values for M19_197
No values for M19_198
No values for M19_199
No values for M19_200
No values for M19_201
No values for M19_202
No values for M19_203
No values for M19_204
No values for M19_205
No values for M19_206
No values for M19_207
No values for M19_208
No values for M19_209
No values for M19_210
No values for M20_169
No values for M20_170
No values for M20_171
No values for M20_172
No values for M20_173
No values for M20_174
No values for M20_175
No values for M20_176
No values for M20_177
No values for M20_178
No values 

No values for M28_171
No values for M28_172
No values for M28_173
No values for M28_174
No values for M28_175
No values for M28_176
No values for M28_177
No values for M28_178
No values for M28_179
No values for M28_180
No values for M28_181
No values for M28_182
No values for M28_183
No values for M28_184
No values for M28_185
No values for M28_186
No values for M28_187
No values for M28_188
No values for M28_189
No values for M28_190
No values for M28_191
No values for M28_192
No values for M28_193
No values for M28_194
No values for M28_195
No values for M28_196
No values for M28_197
No values for M28_198
No values for M28_199
No values for M28_200
No values for M28_201
No values for M28_202
No values for M28_203
No values for M28_204
No values for M28_205
No values for M28_206
No values for M28_207
No values for M28_208
No values for M28_209
No values for M28_210
No values for M29_169
No values for M29_170
No values for M29_171
No values for M29_172
No values for M29_173
No values 

No values for M36_208
No values for M36_209
No values for M36_210
No values for M37_169
No values for M37_170
No values for M37_171
No values for M37_172
No values for M37_173
No values for M37_174
No values for M37_175
No values for M37_176
No values for M37_177
No values for M37_178
No values for M37_179
No values for M37_180
No values for M37_181
No values for M37_182
No values for M37_183
No values for M37_184
No values for M37_185
No values for M37_186
No values for M37_187
No values for M37_188
No values for M37_189
No values for M37_190
No values for M37_191
No values for M37_192
No values for M37_193
No values for M37_194
No values for M37_195
No values for M37_196
No values for M37_197
No values for M37_198
No values for M37_199
No values for M37_200
No values for M37_201
No values for M37_202
No values for M37_203
No values for M37_204
No values for M37_205
No values for M37_206
No values for M37_207
No values for M37_208
No values for M37_209
No values for M37_210
No values 

...

No values for M186_51
No values for M186_52
No values for M186_53
No values for M186_54
No values for M186_55
No values for M186_56
No values for M186_57
No values for M186_58
No values for M186_59
No values for M186_60
No values for M186_61
No values for M186_62
No values for M186_63
No values for M186_64
No values for M186_65
No values for M186_66
No values for M186_67
No values for M186_68
No values for M186_69
No values for M186_70
No values for M186_71
No values for M186_72
No values for M186_73
No values for M186_74
No values for M186_75
No values for M186_76
No values for M186_77
No values for M186_78
No values for M186_79
No values for M186_80
No values for M186_81
No values for M186_82
No values for M186_83
No values for M186_84
No values for M186_85
No values for M186_86
No values for M186_87
No values for M186_88
No values for M186_89
No values for M186_90
No values for M186_91
No values for M186_92
No values for M186_93
No values for M186_94
No values for M186_95
No values 

No values for M188_82
No values for M188_83
No values for M188_84
No values for M188_85
No values for M188_86
No values for M188_87
No values for M188_88
No values for M188_89
No values for M188_90
No values for M188_91
No values for M188_92
No values for M188_93
No values for M188_94
No values for M188_95
No values for M188_96
No values for M188_97
No values for M188_98
No values for M188_99
No values for M188_100
No values for M188_101
No values for M188_102
No values for M188_103
No values for M188_104
No values for M188_105
No values for M188_106
No values for M188_107
No values for M188_108
No values for M188_109
No values for M188_110
No values for M188_111
No values for M188_112
No values for M188_113
No values for M188_114
No values for M188_115
No values for M188_116
No values for M188_117
No values for M188_118
No values for M188_119
No values for M188_120
No values for M188_121
No values for M188_122
No values for M188_123
No values for M188_124
No values for M188_125
No val

No values for M190_113
No values for M190_114
No values for M190_115
No values for M190_116
No values for M190_117
No values for M190_118
No values for M190_119
No values for M190_120
No values for M190_121
No values for M190_122
No values for M190_123
No values for M190_124
No values for M190_125
No values for M190_126
No values for M190_127
No values for M190_128
No values for M190_129
No values for M190_130
No values for M190_131
No values for M190_132
No values for M190_133
No values for M190_134
No values for M190_135
No values for M190_136
No values for M190_137
No values for M190_138
No values for M190_139
No values for M190_140
No values for M190_141
No values for M190_142
No values for M190_143
No values for M190_144
No values for M190_145
No values for M190_146
No values for M190_147
No values for M190_148
No values for M190_149
No values for M190_150
No values for M190_151
No values for M190_152
No values for M190_153
No values for M190_154
No values for M190_155
No values f

No values for M192_143
No values for M192_144
No values for M192_145
No values for M192_146
No values for M192_147
No values for M192_148
No values for M192_149
No values for M192_150
No values for M192_151
No values for M192_152
No values for M192_153
No values for M192_154
No values for M192_155
No values for M192_156
No values for M192_157
No values for M192_158
No values for M192_159
No values for M192_160
No values for M192_161
No values for M192_162
No values for M192_163
No values for M192_164
No values for M192_165
No values for M192_166
No values for M192_167
No values for M192_168
No values for M193_1
No values for M193_2
No values for M193_3
No values for M193_4
No values for M193_5
No values for M193_6
No values for M193_7
No values for M193_8
No values for M193_9
No values for M193_10
No values for M193_11
No values for M193_12
No values for M193_13
No values for M193_14
No values for M193_15
No values for M193_16
No values for M193_17
No values for M193_18
No values for M

No values for M195_5
No values for M195_6
No values for M195_7
No values for M195_8
No values for M195_9
No values for M195_10
No values for M195_11
No values for M195_12
No values for M195_13
No values for M195_14
No values for M195_15
No values for M195_16
No values for M195_17
No values for M195_18
No values for M195_19
No values for M195_20
No values for M195_21
No values for M195_22
No values for M195_23
No values for M195_24
No values for M195_25
No values for M195_26
No values for M195_27
No values for M195_28
No values for M195_29
No values for M195_30
No values for M195_31
No values for M195_32
No values for M195_33
No values for M195_34
No values for M195_35
No values for M195_36
No values for M195_37
No values for M195_38
No values for M195_39
No values for M195_40
No values for M195_41
No values for M195_42
No values for M195_43
No values for M195_44
No values for M195_45
No values for M195_46
No values for M195_47
No values for M195_48
No values for M195_49
No values for M

Now are ready to output our various items. Do the pickle files first

In [37]:
#display( HTML( AllMonDF.head().to_html() )) 

In [39]:
#len( AllMonDF.columns.tolist() ), len( AllMonDF )

(16296, 360)

In [40]:
#len( AllAnnDF.columns.tolist() ), len( AllAnnDF )

(16296, 30)

In [31]:
MonPCKF = os.path.normpath( os.path.join( OUT_DIR, "AllMonth_1981-2010.pickle" ) )
AllMonDF.to_pickle( MonPCKF )
AnnPCKF = os.path.normpath( os.path.join( OUT_DIR, "AllYears_1981-2010.pickle" ) )
AllAnnDF.to_pickle( AnnPCKF )

Next use the feather library for R compatibility

In [32]:
FAllMonDF = AllMonDF.copy()
FAllAnnDF = AllAnnDF.copy()
FAllMonDF = FAllMonDF.reset_index()
FAllAnnDF = FAllAnnDF.reset_index()

In [33]:
MonFeatherF = os.path.normpath( os.path.join( OUT_DIR, "AllMonth_1981-2010.feather" ) )
FAllMonDF.to_feather( MonFeatherF )
AnnFeatherF = os.path.normpath( os.path.join( OUT_DIR, "AllYears_1981-2010.feather" ) )
FAllAnnDF.to_feather( AnnFeatherF )

Finally output to a spreadsheet, transpose the arrays first so that process them easier in Excel

In [42]:
AllMonDF = AllMonDF.transpose()
AllAnnDF = AllAnnDF.transpose()

In [43]:
OutXLSX = os.path.normpath( os.path.join( OUT_DIR, "Precip_Agg_1981-2010.xlsx" ) )
with pd.ExcelWriter(OutXLSX) as writer:
    GridDF.to_excel( writer, sheet_name="Grid_Metadata", na_rep=str(np.nan),
                     index=True, index_label="Id" )
    AllMonDF.to_excel( writer, sheet_name="Monthly", na_rep=str(np.nan),
                       index=True, index_label="Model_and_Grid" )
    AllAnnDF.to_excel( writer, sheet_name="Annual", na_rep=str(np.nan),
                       index=True, index_label="Model_and_Grid" )
# end of with and write output

In [44]:
# delete some data frames to help with memory issues
del AllMonDF
del AllAnnDF
del FAllAnnDF
del FAllMonDF

## Wet and Dry Days

While the monthly and annual aggregation was being completed, also collated the contiguous wet and dry day counts. These are in a dictionary. Need to process these out so that can work with them further

Determine the maximum number of wet days

In [46]:
AllKeys = sorted( WetDict.keys() )
len( AllKeys )

16296

In [47]:
AllKeys == sorted( DryDict.keys() )

True

In [48]:
MaxWetDays = 0
TotWetSeqs = 0
for tKey in AllKeys:
    TotWetSeqs = TotWetSeqs + len( WetDict[tKey] )
    NewWetDays = max( [x[1] for x in WetDict[tKey]] )
    if NewWetDays > MaxWetDays:
        MaxWetDays = NewWetDays
# end of for
MaxWetDays, TotWetSeqs

(69, 23161112)

Go through our dictionaries and create DataFrames for each grid cell and then concatenate these all together.

In [49]:
DDFList = list()
WDFList = list()

In [50]:
for tKey in AllKeys:
    tDryList = DryDict[tKey]
    dNEnts = len( tDryList )
    DataDict = { "MGrid_Id" : [ tKey for x in range(dNEnts) ],
                 "Year" : [x[0].year for x in tDryList],
                 "Month" : [x[0].month for x in tDryList],
                 "Day" : [x[0].day for x in tDryList],
                 "Dry_Count" : [x[1] for x in tDryList], }
    tDryDF = pd.DataFrame( data=DataDict )
    #tDryDF["Month"] = tDryDF.apply( lambda row: ExIntMonth( row["Start_Date"] ), axis=1 )
    DDFList.append( tDryDF )
    tWetList = WetDict[tKey]
    wNEnts = len( tWetList )
    WDaysArray = np.zeros( (wNEnts, MaxWetDays), dtype=np.float32 )
    # fill in the wet days array
    for iI in range(wNEnts):
        wdsList = tWetList[iI][3]
        cNDays = len( wdsList )
        for jJ in range( cNDays ):
            cdDep = wdsList[jJ]
            WDaysArray[iI, jJ] = cdDep
        # end of days for
    # end of rows for
    # now can create our DataFrame
    DataDict = { "MGrid_Id" : [ tKey for x in range(wNEnts) ],
                 "Year" : [x[0].year for x in tWetList],
                 "Month" : [x[0].month for x in tWetList],
                 "Day" : [x[0].day for x in tWetList],
                 "Wet_Count" : [x[1] for x in tWetList], 
                 "Total_Depth" : [x[2] for x in tWetList], }
    for dD in range(1, (MaxWetDays + 1)):
        DayLabel = "Day_%d" % dD
        DataDict[DayLabel] = WDaysArray[:, (dD-1)]
    # end of day label for
    tWetDF = pd.DataFrame( data=DataDict )
    #tWetDF["Month"] = tWetDF.apply( lambda row: ExIntMonth( row["Start_Date"] ), axis=1 )
    WDFList.append( tWetDF )
# end of outer for

In [51]:
WetDayDF = pd.concat( WDFList, ignore_index=True )
DryDayDF = pd.concat( DDFList, ignore_index=True )

In [52]:
len( WetDayDF ), len( DryDayDF )

(23161112, 23170457)

In [53]:
display( HTML( WetDayDF.head().to_html() ) )

In [54]:
display( HTML( WetDayDF.tail().to_html() ) )

In [55]:
display( HTML( DryDayDF.head().to_html() ) )

In [56]:
DryDayDF['Dry_Count'].sum() + WetDayDF['Wet_Count'].sum()

178555272

Now output to pickle files in case need to reload

In [57]:
DryPCKF = os.path.normpath( os.path.join( OUT_DIR, "DryDays_1981-2010.pickle" ) )
DryDayDF.to_pickle( DryPCKF )
WetPCKF = os.path.normpath( os.path.join( OUT_DIR, "WetDays_1981-2010.pickle" ) )
WetDayDF.to_pickle( WetPCKF )

And output to feather format for integration with R.

In [58]:
DryFeatherF = os.path.normpath( os.path.join( OUT_DIR, "DryDays_1981-2010.feather" ) )
DryDayDF.to_feather( DryFeatherF )
DryFeatherF = os.path.normpath( os.path.join( OUT_DIR, "WetDays_1981-2010.feather" ) )
WetDayDF.to_feather( DryFeatherF )